In [1]:
using Pkg
using JuMP
using Gurobi
#using GLPK
using XLSX
using DataFrames
using CSV

In [2]:
using LinearAlgebra

In [3]:
shared_cand = DataFrame(XLSX.readtable("../Input_Data/CandLine.csv", "Taul1", header=true)) #Dataframe of shared candidate lines
int_cand =  DataFrame(XLSX.readtable("../Input_Data/CandLineInt.csv", "Taul1", header=true)) #Dataframe of internal candidate lines
shared_ex =  DataFrame(XLSX.readtable("../Input_Data/SharedEline.csv", "Taul1", header=true)) #Dataframe of shared existing lines
int_ex = DataFrame(XLSX.readtable("../Input_Data/Tran.csv", "Taul1", header=true)) #Dataframe of internal existing lines
gen =  DataFrame(XLSX.readtable("../Input_Data/Gen.csv" , "Taul1", header=true)) #Dataframe of generators
load =  DataFrame(XLSX.readtable("../Input_Data/Load.csv", "Taul1", header=true)) #Dataframe of loads
scen_prob = DataFrame(CSV.File("../Input_Data/Scenario_Probability.csv", header=true)) #Dataframe of scenario probabilities
zone_summary = DataFrame(CSV.File("../Input_Data/Zone_Summary.csv", header=true)) #Dataframe of region-number of nodes

3×2 DataFrame
 Row │ Zone   Nodes_Total 
     │ Int64  Int64       
─────┼────────────────────
   1 │     1           14
   2 │     2           30
   3 │     3            5

In [4]:
l(i,s) = load[load.zoneNum .== i,[1,2,s+2]] # load within zone i and scenario s
g(i) = gen[gen.zoneNum .== i, :]   # generators within zone i
shared_c(i) = vcat(shared_cand[shared_cand.nodeZone1 .== i,:] , shared_cand[shared_cand.nodeZone2 .== i, :]) #shared candidate lines within zone i
int_c(i) = int_cand[int_cand.zoneNum .== i, :]   # number of internal candidate lines within zone i
shared_e(i) = vcat(shared_ex[shared_ex.nodeZone1 .== i,:] , shared_ex[shared_ex.nodeZone2 .== i, :]) #shared existing lines within zone i
int_e(i) =int_ex[int_ex.zoneNum .== i, :]       # internal existing lines within zone i
MC(i) = (g(i).C2 .* (g(i).PgMax .^ 2) .+ g(i).C1 .* g(i).PgMax .- g(i).C2 .*(g(i).PgMin .^ 2) .- g(i).C1 .* g(i).PgMin) ./ (g(i).PgMax .- g(i).PgMin) #Marginal cost of generators within zone i
bin_c(i) = (shared_cand.nodeZone1 .== i) + (shared_cand.nodeZone2 .== i) # A binary vector through which we can check if the shared candidate lines belong to zone i
bin_e(i) = (shared_ex.nodeZone1 .== i) + (shared_ex.nodeZone2 .== i) # A binary vector through which we can check if the shared existing lines belong to zone i
scen_weight(s) = scen_prob.scen_weight[scen_prob.scenario .== s,:]

scen_weight (generic function with 1 method)

In [5]:
S = nrow(scen_prob)

4

In [6]:
function bin(i,N,S)
    P = zeros(nrow(zone_summary),maximum(zone_summary.Nodes_Total),S); 
    #P[i,1:N,:] .= 1
    for c in 1:nrow(shared_c(i))
        P[shared_c(i).nodeZone1[c],shared_c(i).tNodeID1[c],:] .= 1
        P[shared_c(i).nodeZone2[c],shared_c(i).tNodeID2[c],:] .= 1
    end
    for h in 1:nrow(shared_e(i))
        P[shared_e(i).nodeZone1[h],shared_e(i).tNodeID1[h],:] .= 1
        P[shared_e(i).nodeZone2[h],shared_e(i).tNodeID2[h],:] .= 1
    end
    return(P)
end

bin (generic function with 1 method)

In [7]:
shared = bin(1,14,S).*bin(2,30,S).*bin(3,5,S)
not_shared = (1 .- shared)

3×30×4 Array{Float64, 3}:
[:, :, 1] =
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  …  1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0

[:, :, 2] =
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  …  1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0

[:, :, 3] =
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  …  1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0

[:, :, 4] =
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0  …  1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  1.0  1.0  1.0  1.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1.0  1.0  1.0
 1.0  0.0  1.0  0.0  0.0  1.0  1.0  1.0     1.0  1.0  1.0  1.0  1

In [8]:
function zonal_app(i, N, S, lambda, shared_line_decision_var, int_line_decision_var, angle_self, angle_1, angle_2, bin_self, bin_1, bin_2)
    
    Mod4 = Model(Gurobi.Optimizer)
    ###Change it to IPOPT
    
    
    @variable(Mod4,0 <= gen_var[1:N,1:S]) # generation at each node
    @variable(Mod4,shared_cand_flow[1:nrow(shared_cand),1:S])  #Power flowing into shared candidate lines 
    @variable(Mod4,int_cand_flow[1:nrow(int_c(i)), 1:S]) #Power flowing into internal candidate lines 
    #@variable(Mod4,0 <= shared_cand_angle[1:nrow(shared_cand), 1:S, 1:2]<= 2*pi) #Phase angle decision for shared candidate lines
    #@variable(Mod4,0 <= int_cand_angle[1:nrow(int_c(i)), 1:S, 1:2]<= 2*pi) #Phase angle decision for internal candidate lines
    @variable(Mod4,shared_ex_flow[1:nrow(shared_ex), 1:S])  #Power flowing on shared existing shared lines
    @variable(Mod4,int_ex_flow[1:nrow(int_e(i)), 1:S])  #Power flowing on internal existing lines
    @variable(Mod4,0 <= node_voltage_phase_angle[1:nrow(zone_summary),1:maximum(zone_summary.Nodes_Total), 1:S] <= 2*pi)
   # @variable(Mod4,0 <= shared_ex_angle[1:nrow(shared_ex), 1:S, 1:2]<= 2*pi) #Phase angle for existing shared lines
    #@variable(Mod4,0 <= int_ex_angle[1:nrow(int_e(i)), 1:S, 1:2]<= 2*pi) #Phase angle for internal existing lines
    
    omega = 1;
    eta = 1;
    
    @expression(Mod4, total_cost, sum(scen_weight(s)[1].* sum((gen_var[n,s] .* sum((g(i).gNodeID .== n) .* MC(i) ./ 100)) for n in 1:N) for s in 1:S)
        .+ sum(sum(sum(eta * bin_self .* bin_1 .* (node_voltage_phase_angle .* (angle_self .- angle_1))
        .+ eta * bin_self .* bin_2 .* (node_voltage_phase_angle.* (angle_self .- angle_2))
        .+ (omega /2) * (bin_self .* (node_voltage_phase_angle.- angle_self)) .^ 2
        .+ (omega /2) * (bin_self .* bin_1 .* (node_voltage_phase_angle.- angle_1)) .^ 2
        .+ (omega /2) * (bin_self .* bin_2 .* (node_voltage_phase_angle .- angle_2)) .^ 2
        .+ node_voltage_phase_angle .* lambda))))
             
            
    for s in 1:S        
            
        for n in 1:N
            # Power balance constraint for each node
            @constraint(Mod4, sum((g(i).gNodeID .== n) .* gen_var[n,s]) .+ sum(l(i,s)[:,3].* (l(i,s).lNodeID .== n))./100 .==
                sum((shared_cand.tNodeID1 .== n) .*bin_c(i) .* shared_cand_flow[:,s]) .- sum((shared_cand.tNodeID2 .== n) .* bin_c(i) .* shared_cand_flow[:,s]) .+
                sum((shared_ex.tNodeID1 .== n) .* bin_e(i) .* shared_ex_flow[:,s]) .- sum((shared_ex.tNodeID2 .== n) .* bin_e(i) .* shared_ex_flow[:,s]) .+
                sum((int_c(i).tNodeID1 .== n) .* int_cand_flow[:,s]) .- sum((int_c(i).tNodeID2 .== n) .* int_cand_flow[:,s]) .+
                sum((int_e(i).tNodeID1 .== n) .* int_ex_flow[:,s]) .- sum((int_e(i).tNodeID2 .== n) .* int_ex_flow[:,s]))
            #Lower limit for generation of each node
            @constraint(Mod4, sum(g(i).gNodeID .== n) .* gen_var[n,s] .<= sum((g(i).gNodeID .== n) .* g(i).PgMax./100))
            #Upper limit for generation of each node
            @constraint(Mod4, sum((g(i).gNodeID .== n) .* g(i).PgMin./100) .<= sum(g(i).gNodeID .== n) .* gen_var[n,s])
        end

        M = 10 #Big number

        #Constraints elated to the candidate shared lines:
        for c in 1:nrow(shared_cand) 
            #Associating the power flowing within the line with the phase angles of nodes:
            @constraint(Mod4,-M .* (1 .- bin_c(i) .* shared_line_decision_var[c]) .<= bin_c(i) .* shared_cand_flow[c,s] .- 
                ((1 ./ shared_cand.reacT[c]) .* bin_c(i) .* 
                (node_voltage_phase_angle[shared_cand.nodeZone1[c],shared_cand.tNodeID1[c],s] 
                .- node_voltage_phase_angle[shared_cand.nodeZone2[c],shared_cand.tNodeID2[c],s])))
            @constraint(Mod4, bin_c(i) .* shared_cand_flow[c,s] .- ((1 ./ shared_cand.reacT[c]) .*
                (bin_c(i) .* (node_voltage_phase_angle[shared_cand.nodeZone1[c],shared_cand.tNodeID1[c],s] .- 
                node_voltage_phase_angle[shared_cand.nodeZone2[c],shared_cand.tNodeID2[c],s]))) 
                .<= M .* (1 .- bin_c(i) .* shared_line_decision_var[c]))
            #limiting the upper bound of power flow flowing within candidate shared lines
            @constraint(Mod4, bin_c(i) .* shared_cand_flow[c,s] .<= bin_c(i) .* 
                shared_line_decision_var[c] .* shared_cand.ptMax[c] ./ 100)
            #Limiting the lower bound of power flowing within the candidate shared lines
            @constraint(Mod4, -shared_cand.ptMax[c] .* bin_c(i) .* shared_line_decision_var[c] ./ 100 .<= bin_c(i) .* 
                shared_cand_flow[c,s])
            #@constraint(Mod4, shared_cand_angle[5,2] .== 0)
        end

        #The same constraints related to the candidate internal lines:
        for c in 1:nrow(int_c(i))
            @constraint(Mod4,-M .* (1 .- int_line_decision_var[c]) .<= int_cand_flow[c,s] .- ((1 ./ int_c(i).reacT[c]) .*
                    (node_voltage_phase_angle[int_c(i).zoneNum[c],int_c(i).tNodeID1[c],s] .-
                    node_voltage_phase_angle[int_c(i).zoneNum[c],int_c(i).tNodeID2[c],s])))
            @constraint(Mod4, int_cand_flow[c,s] .- ((1 ./ int_c(i).reacT[c]) .* 
                    (node_voltage_phase_angle[int_c(i).zoneNum[c],int_c(i).tNodeID1[c],s] .- 
                    node_voltage_phase_angle[int_c(i).zoneNum[c],int_c(i).tNodeID2[c],s]))
                    .<= M .* (1 .- int_line_decision_var[c]))
            @constraint(Mod4, int_cand_flow[c,s] .<= int_line_decision_var[c] .* int_c(i).ptMax[c] ./ 100)
            @constraint(Mod4, -int_c(i).ptMax[c] .*int_line_decision_var[c] ./ 100 .<= int_cand_flow[c,s])
        end

        #The same constraints related to the shared existing lines:
        for h in 1:nrow(shared_ex)
            @constraint(Mod4, bin_e(i) .* shared_ex_flow[h,s] .== (1 ./ shared_ex.reacT[h]) .*
                (bin_e(i) .* (node_voltage_phase_angle[shared_ex.nodeZone1[h],shared_ex.tNodeID1[h],s] .-
                node_voltage_phase_angle[shared_ex.nodeZone2[h],shared_ex.tNodeID2[h],s])))
            @constraint(Mod4, bin_e(i) .* shared_ex_flow[h,s] .<= bin_e(i) .* shared_ex. ptMax[h] ./ 100)
            @constraint(Mod4, bin_e(i) .* -shared_ex.ptMax[h] ./ 100 .<= bin_e(i) .* shared_ex_flow[h,s])
            #@constraint(Mod4, shared_ex_angle[1,2] .== 0)
            #@constraint(Mod4, shared_ex_angle[7,2] .== 0)

        end
        #The same constraints related to the internal existing lines:

        for h in 1:nrow(int_e(i))
            @constraint(Mod4, int_ex_flow[h,s] .== (1 ./ int_e(i).reacT[h]) 
                .* (node_voltage_phase_angle[int_e(i).zoneNum[h],int_e(i).tNodeID1[h],s] .- 
                    node_voltage_phase_angle[int_e(i).zoneNum[h],int_e(i).tNodeID2[h],s]))
            @constraint(Mod4, int_ex_flow[h,s] .<= int_e(i).ptMax[h] ./ 100)
            @constraint(Mod4, -int_e(i).ptMax[h] ./ 100 .<= int_ex_flow[h,s])
        end
    end
    #The model objective is to minimize the total cost:
    
    @objective(Mod4, Min, total_cost)
    optimize!(Mod4)
    if termination_status(Mod4) == MOI.OPTIMAL #If the solution is optimal then it returns the variables
    
        shared_cand_power = value.(shared_cand_flow)
        shared_ex_power = value.(shared_ex_flow)
        phase_angle = value.(node_voltage_phase_angle)
        gen_power = value.(gen_var)
        int_cand_power = value.(int_cand_flow)
        obj_value = objective_value(Mod4)
        [obj_value,shared_cand_power,phase_angle,shared_ex_power,gen_power, int_cand_power]

    end
end
    
    

zonal_app (generic function with 1 method)

In [9]:
f=ones(12000)
h=0
lambda_1= zeros(12000,nrow(zone_summary),maximum(zone_summary.Nodes_Total),S)
lambda_2= zeros(12000,nrow(zone_summary),maximum(zone_summary.Nodes_Total),S)
lambda_3 = zeros(12000,nrow(zone_summary),maximum(zone_summary.Nodes_Total),S)

angle_1 = zeros(12000,nrow(zone_summary),maximum(zone_summary.Nodes_Total),S)
angle_2 = zeros(12000,nrow(zone_summary),maximum(zone_summary.Nodes_Total),S)
angle_3 = zeros(12000,nrow(zone_summary),maximum(zone_summary.Nodes_Total),S)

cand_flow_1 =zeros(12000,nrow(shared_cand),S)
cand_flow_2 =zeros(12000,nrow(shared_cand),S)
cand_flow_3 =zeros(12000,nrow(shared_cand),S)

ex_flow_1 = zeros(12000,nrow(shared_ex),S)
ex_flow_2 = zeros(12000,nrow(shared_ex),S)
ex_flow_3 = zeros(12000,nrow(shared_ex),S)

int_cand_flow_1 = zeros(12000,nrow(int_c(1)),S)
int_cand_flow_2 = zeros(12000,nrow(int_c(2)),S)
int_cand_flow_3 = zeros(12000,nrow(int_c(3)),S)

gen_1 = zeros(12000,zone_summary.Nodes_Total[1],S)
gen_2 = zeros(12000,zone_summary.Nodes_Total[2],S)
gen_3 = zeros(12000,zone_summary.Nodes_Total[3],S)

iter = 0



shared_line_decision_var_m =  
[0.0
 0.0
 0.0
 1.0
 1.0
 0.0]
int_line_decision_var_1 =
[0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 1.0]
int_line_decision_var_2 =
[1.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 1.0
 1.0
 0.0
 0.0
 1.0
 0.0
 1.0
 0.0
 0.0]
int_line_decision_var_3 =
[0.0
 0.00]

2-element Vector{Float64}:
 0.0
 0.0

In [10]:
    j = 2
    max_iter = 1000
    for j in 2:max_iter    # It considers 1000 iteration
        if abs(f[j-1]) > 0.0001  
         
            R_1 = zonal_app(1, 14, S, lambda_1[j,:,:,:], shared_line_decision_var_m, int_line_decision_var_1,
            angle_1[j-1,:,:,:], angle_2[j-1,:,:,:], angle_3[j-1,:,:,:], bin(1,14,S), bin(2,30,S), bin(3,5,S))
        
            R_2 = zonal_app(2, 30, S, lambda_2[j,:,:,:], shared_line_decision_var_m, int_line_decision_var_2,
            angle_2[j-1,:,:,:], angle_1[j-1,:,:,:], angle_3[j-1,:,:,:], bin(2,30,S), bin(1,14,S), bin(3,5,S))
        
            R_3 = zonal_app(3, 5, S, lambda_3[j,:,:,:], shared_line_decision_var_m, int_line_decision_var_3,
            angle_3[j-1,:,:,:], angle_1[j-1,:,:,:], angle_2[j-1,:,:,:], bin(3,5,S), bin(1,14,S), bin(2,30,S))
        
            
        
        
            lambda_1[j+1,:,:,:] .= bin(1,14,S) .* lambda_1[j,:,:,:] 
                .+ 0.00001 * bin(1,14,S) .* not_shared .* (R_1[3] .- (bin(2,30,S) .* R_2[3] .+ bin(3,5,S) .* R_3[3]))
                .+ 0.00001 * bin(1,14,S) .* shared .* (R_1[3] .- (bin(2,30,S) .* R_2[3] .+ bin(3,5,S) .* R_3[3]) ./ 2)
            lambda_2[j+1,:,:,:] .= bin(2,30,S) .* lambda_2[j,:,:,:] 
                .+ 0.00001 * bin(2,30,S) .* not_shared .* (R_2[3] .- (bin(1,14,S) .* R_1[3] .+ bin(3,5,S) .* R_3[3]))
                .+ 0.00001 * bin(2,30,S) .* shared .* (R_2[3] .- (bin(1,14,S) .* R_1[3] .+ bin(3,5,S) .* R_3[3]) ./ 2)
            lambda_3[j+1,:,:,:] .= bin(3,5,S) .* lambda_3[j,:,:,:] 
                .+ 0.00001 * bin(3,5,S).* not_shared .* (R_3[3] .- (bin(1,14,S) .* R_1[3] .+ bin(2,30,S) .* R_2[3]))
                .+ 0.00001 * bin(3,5,S).* shared .* (R_3[3] .- (bin(1,14,S) .* R_1[3] .+ bin(2,30,S) .* R_2[3]) ./ 2)
        
        
        
            angle_1[j,:,:,:] = R_1[3]
            angle_2[j,:,:,:] = R_2[3]
            angle_3[j,:,:,:] = R_3[3]
            
            cand_flow_1[j,:,:] = R_1[2] .* 100
            cand_flow_2[j,:,:] = R_2[2] .* 100
            cand_flow_3[j,:,:] = R_3[2] .* 100
        
            ex_flow_1[j,:,:] = R_1[4] .* 100
            ex_flow_2[j,:,:] = R_2[4] .* 100
            ex_flow_3[j,:,:] = R_3[4] .* 100
        
            gen_1[j,:,:] = R_1[5] .* 100
            gen_2[j,:,:] = R_2[5] .* 100
            gen_3[j,:,:] = R_3[5] .* 100
        
            
            f[j] = sum(sum(bin(1,14,S) .* not_shared .* (R_1[3] .- (bin(2,30,S) .* R_2[3] .+ bin(3,5,S) .* R_3[3])) .^ 2)) +
                    sum(sum(bin(2,30,S) .* not_shared .* (R_2[3] .- (bin(1,14,S) .* R_1[3] .+ bin(3,5,S) .* R_3[3])) .^ 2)) +
                    sum(sum(bin(3,5,S).* not_shared .* (R_3[3] .- (bin(1,14,S) .* R_1[3] .+ bin(2,30,S) .* R_2[3])) .^ 2)) +
                    sum(sum(bin(1,14,S) .* shared .* (R_1[3] .- (bin(2,30,S) .* R_2[3] .+ bin(3,5,S) .* R_3[3])./ 2) .^ 2)) +
                    sum(sum(bin(2,30,S) .* shared .* (R_2[3] .- (bin(1,14,S) .* R_1[3] .+ bin(3,5,S) .* R_3[3])./ 2) .^ 2)) +
                    sum(sum(bin(3,5,S).* shared .* (R_3[3] .- (bin(1,14,S) .* R_1[3] .+ bin(2,30,S) .* R_2[3])./ 2) .^ 2))

            h= R_2[1] + R_1[1] + R_3[1]
            
            if isdefined(Main, :IJulia)
                Main.IJulia.stdio_bytes[] = 0
            end
        
            print('*') 
        
        else
            iter = j-1
            print(iter)
            break
        end
    end
    

Academic license - for non-commercial use only - expires 2023-06-28
Gurobi Optimizer version 9.1.2 build v9.1.2rc0 (win64)
Thread count: 4 physical cores, 4 logical processors, using up to 4 threads
Optimize a model with 1912 rows, 592 columns and 2608 nonzeros
Model fingerprint: 0xbc2e5217
Model has 52 quadratic objective terms
Coefficient statistics:
  Matrix range     [1e+00, 2e+01]
  Objective range  [9e-02, 1e-01]
  QObjective range [2e+00, 3e+00]
  Bounds range     [6e+00, 6e+00]
  RHS range        [9e-03, 1e+01]
Presolve removed 1712 rows and 408 columns
Presolve time: 0.02s
Presolved: 200 rows, 236 columns, 652 nonzeros
Presolved model has 52 quadratic objective terms
Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 9.120e+02
 Factor NZ  : 2.872e+03
 Factor Ops : 4.713e+04 (less than 1 second per iteration)
 Threads    : 1

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   1.51899461e+07 -

In [11]:
if iter == 0
    iter = max_iter
end

1000

In [12]:
iter

1000

In [13]:
h #OF of the second stage

0.17028326850875386

In [14]:
f[iter]

0.0016733810759376423

In [38]:
f[991]

0.001666147665424651

In [15]:
bin(1,14,S) .* bin(3,5,S) .* (angle_1[iter,:,:,:]-angle_3[iter,:,:,:])

3×30×4 Array{Float64, 3}:
[:, :, 1] =
 5.61455e-5   4.6162e-5     0.0  …  0.0   0.0  0.0  0.0  0.0  0.0  0.0
 0.0          0.0           0.0     0.0  -0.0  0.0  0.0  0.0  0.0  0.0
 0.00782198  -0.000279885  -0.0     0.0   0.0  0.0  0.0  0.0  0.0  0.0

[:, :, 2] =
  1.42966e-5   1.62895e-5    0.0  …  0.0   0.0  0.0  0.0  0.0  0.0  0.0
  0.0          0.0           0.0     0.0  -0.0  0.0  0.0  0.0  0.0  0.0
 -0.00224878  -0.000617811  -0.0     0.0   0.0  0.0  0.0  0.0  0.0  0.0

[:, :, 3] =
 -0.00243431   5.92877e-5    0.0  …  0.0   0.0  0.0  0.0  0.0  0.0  0.0
  0.0          0.0           0.0     0.0  -0.0  0.0  0.0  0.0  0.0  0.0
 -0.00243421  -0.000944831  -0.0     0.0   0.0  0.0  0.0  0.0  0.0  0.0

[:, :, 4] =
 -3.53488e-6   1.70612e-6    0.0  …  0.0   0.0  0.0  0.0  0.0  0.0  0.0
  0.0          0.0           0.0     0.0  -0.0  0.0  0.0  0.0  0.0  0.0
 -0.00111201  -0.000436543  -0.0     0.0   0.0  0.0  0.0  0.0  0.0  0.0

In [16]:
angle_1[iter,:,:,:]

3×30×4 Array{Float64, 3}:
[:, :, 1] =
 0.134423  0.0941445  8.23623e-5  …  0.0       0.0  0.0  0.0  0.0  0.0
 0.0       0.0        0.0            0.156916  0.0  0.0  0.0  0.0  0.0
 0.342423  0.356916   0.0            0.0       0.0  0.0  0.0  0.0  0.0

[:, :, 2] =
 0.046978  0.0394187  6.33207e-10  …  0.0        0.0  0.0  0.0  0.0  0.0
 0.0       0.0        0.0             0.0703646  0.0  0.0  0.0  0.0  0.0
 0.237937  0.270365   0.0             0.0        0.0  0.0  0.0  0.0  0.0

[:, :, 3] =
 0.0883952  0.0660313  0.000107314  …  0.0       0.0  0.0  0.0  0.0  0.0
 0.0        0.0        0.0             0.134039  0.0  0.0  0.0  0.0  0.0
 0.296395   0.334039   0.0             0.0       0.0  0.0  0.0  0.0  0.0

[:, :, 4] =
 0.0232798  0.0196438  3.42974e-8  …  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0        0.0        0.0            0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.121037   0.137516   0.0            0.0  0.0  0.0  0.0  0.0  0.0  0.0

In [17]:
angle_2[iter,:,:,:]

3×30×4 Array{Float64, 3}:
[:, :, 1] =
 0.679164  1.44662   0.0       0.0       …  0.0       0.0       0.0
 0.573517  0.583575  0.54462   0.52225      0.514199  0.437756  0.421144
 0.471164  0.360193  0.329312  0.319489     0.0       0.0       0.0

[:, :, 2] =
 0.615741  1.39708   0.0       0.0       …  0.0       0.0       0.0
 0.457382  0.469051  0.423855  0.407015     0.406027  0.356289  0.347983
 0.407741  0.271228  0.24767   0.242852     0.0       0.0       0.0

[:, :, 3] =
 0.662493  1.43982   0.0       0.0       …  0.0       0.0       0.0
 0.565047  0.576599  0.531857  0.510164     0.505502  0.436424  0.423965
 0.454493  0.336622  0.307738  0.300495     0.0       0.0       0.0

[:, :, 4] =
 0.520798  1.30824   0.0       0.0       …  0.0       0.0       0.0
 0.235031  0.241786  0.215621  0.206654     0.206878  0.182321  0.178168
 0.312798  0.13825   0.125882  0.123587     0.0       0.0       0.0

In [18]:
angle_3[iter,:,:,:]

3×30×4 Array{Float64, 3}:
[:, :, 1] =
 0.134367  0.0940983  0.0       …  0.0       0.0  0.0  0.0  0.0  0.0
 0.0       0.0        0.0          0.468593  0.0  0.0  0.0  0.0  0.0
 0.334601  0.357196   0.325701     0.0       0.0  0.0  0.0  0.0  0.0

[:, :, 2] =
 0.0469638  0.0394024  0.0       …  0.0       0.0  0.0  0.0  0.0  0.0
 0.0        0.0        0.0          0.361849  0.0  0.0  0.0  0.0  0.0
 0.240186   0.270982   0.247506     0.0       0.0  0.0  0.0  0.0  0.0

[:, :, 3] =
 0.0908295  0.065972  0.0       …  0.0       0.0  0.0  0.0  0.0  0.0
 0.0        0.0       0.0          0.449733  0.0  0.0  0.0  0.0  0.0
 0.298829   0.334984  0.306525     0.0       0.0  0.0  0.0  0.0  0.0

[:, :, 4] =
 0.0232833  0.0196421  0.0       …  0.0      0.0  0.0  0.0  0.0  0.0
 0.0        0.0        0.0          0.18518  0.0  0.0  0.0  0.0  0.0
 0.122149   0.137952   0.125759     0.0      0.0  0.0  0.0  0.0  0.0

In [19]:
bin_c(1)

6-element Vector{Int64}:
 1
 1
 1
 1
 0
 0

In [20]:
bin_c(2)

6-element Vector{Int64}:
 0
 0
 0
 1
 1
 1

In [21]:
bin_c(3)

6-element Vector{Int64}:
 1
 1
 1
 0
 1
 1

In [22]:
cand_flow_1[iter,:,:]

6×4 Matrix{Float64}:
    0.0     0.0        0.0    0.0
    0.0     0.0        0.0    0.0
    0.0     0.0        0.0    0.0
  100.0    88.0808   100.0   44.0171
 -100.0  -100.0     -100.0  -75.0191
    0.0     0.0        0.0    0.0

In [23]:
cand_flow_2[iter,:,:]

6×4 Matrix{Float64}:
  0.0      0.0      0.0      0.0
  0.0      0.0      0.0      0.0
  0.0      0.0      0.0      0.0
 77.6854  62.9155  88.3588  31.2471
 88.8806  67.0258  87.932   33.3292
  0.0      0.0      0.0      0.0

In [24]:
cand_flow_3[iter,:,:]

6×4 Matrix{Float64}:
  0.0        0.0      0.0      0.0
  0.0        0.0      0.0      0.0
  0.0        0.0      0.0      0.0
  0.0     -100.0      0.0      0.0
 94.7508    66.2624  89.5352  33.0312
  0.0        0.0      0.0      0.0

In [25]:
ex_flow_1[iter,:,:]

8×4 Matrix{Float64}:
   52.9152    41.4192    49.5965    20.7329
  -63.2945   -47.6472   -62.2856   -24.1851
  100.0       91.8072   100.0       46.9985
   38.0448    32.4595    38.7006    16.5285
  -72.0184   -46.9704   -59.5921   -24.096
 -100.0     -100.0     -100.0      -68.7578
 -100.0     -100.0     -100.0     -100.0
    0.0        0.0        0.0        0.0

In [26]:
ex_flow_2[iter,:,:]

8×4 Matrix{Float64}:
   49.3146    37.443     47.7535    18.7162
  -62.4969   -47.6304   -61.4662   -24.161
 -100.0     -100.0     -100.0     -100.0
 -100.0     -100.0       54.0458    22.2279
 -100.0     -100.0     -100.0     -100.0
   51.4339    45.8219    56.2956    23.7636
  100.0       75.6549   100.0       38.1318
  -43.9314   -25.3394   -38.9475   -12.513

In [27]:
ex_flow_3[iter,:,:]

8×4 Matrix{Float64}:
 -100.0       0.0       0.0     -100.0
 -100.0      44.8592   55.241     22.6057
   96.2664   92.8952  100.0       47.5315
   37.8186   32.3756   38.3003    16.5072
  -33.9496  -54.3781  -63.4649   -27.8431
   55.6982   45.4332   57.3742    23.614
  100.0      75.1279  100.0       37.9076
  -48.5006  -25.1824  -40.3055   -12.448

In [28]:
gen_1[iter,:,:]

14×4 Matrix{Float64}:
 106.085       8.25924e-10  44.6535      8.19008e-10
   1.26526e-9  5.12302e-10   1.26492e-9  5.094e-10
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0
   0.0         0.0           0.0         0.0

In [29]:
gen_2[iter,:,:]

30×4 Matrix{Float64}:
  5.53609e-5   8.53434e-6   8.19693e-6   2.91018e-7
 80.0         80.0         80.0         47.3
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
 40.0         14.6         39.9995       8.6696e-7
  ⋮                                     
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
 50.0          1.12464e-5  21.9005       3.15348e-7
 19.1999       1.79826e-6   2.37047e-7   2.22914e-7
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0     

In [30]:
gen_3[iter,:,:]

5×4 Matrix{Float64}:
 1.52513e-10  1.44943e-10  1.4616e-10   1.45314e-10
 6.59758e-11  6.40628e-11  6.43299e-11  6.41438e-11
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0
 0.0          0.0          0.0          0.0

In [31]:
gen_2[iter,:,:]

30×4 Matrix{Float64}:
  5.53609e-5   8.53434e-6   8.19693e-6   2.91018e-7
 80.0         80.0         80.0         47.3
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
 40.0         14.6         39.9995       8.6696e-7
  ⋮                                     
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
 50.0          1.12464e-5  21.9005       3.15348e-7
 19.1999       1.79826e-6   2.37047e-7   2.22914e-7
  0.0          0.0          0.0          0.0
  0.0          0.0          0.0          0.0
  0.0     